In [49]:
import re
import pandas as pd
import folium

%store -r totals_data
%store -r series_data
%store -r tests_data

country_data, name_data, series_data, latitude_data, longitude_data, yield_data = ([] for i in range(6))

for country, tests in tests_data.items():
    for test in tests:
        if not any(x in test['Name'] for x in ('aborted', 'canceled')):
            coordinates = re.search('([+-]?\d+\.?\d+)(;)\s([+-]?\d+\.?\d+)', test['Location'])
            coordinates = coordinates.group().replace(' ','').split(';')
            latitude, longitude = (coordinates[i] for i in (0,1))
            
            # standardized to k
            units_dict = {'kg': 0.000001, 't': 0.001, 'kt': 1.0, 'Mt': 1000}
            # Do not include any tests with unknown yields
            if not any(x in test['Yield'] for x in ('no yield','unknown yield','less than')):
                # check if yield is a range of numbers: average LB and UB
                if '-' in test['Yield']:
                    match = re.search('(\d+(?:\.\d+)?)+\s*-\s*(\d+(?:\.\d+)?)\s*(kg|t|kt|Mt)', test['Yield'])
                    yield_ = (float(match.group(1)) + float(match.group(2))) / 2.0 * units_dict[match.group(3)]
                else:
                    match = re.search('(\d+(?:\.\d+)?)\s*(kg|t|kt|Mt)', test['Yield'])
                    yield_ = float(match.group(1)) * units_dict[match.group(2)]
               
                    country_data.append(country)
                    name_data.append(test['Name'])
                    series_data.append('N/A' if not test['Series'] else test['Series'])
                    latitude_data.append(latitude)
                    longitude_data.append(longitude)
                    yield_data.append(yield_)
                    elevation_data.append(elevation)
                    height_data.append(height)

# Make a data frame with bubbles to show on the map
data = pd.DataFrame({
    'country': country_data,
    'name': name_data,
    'series': series_data,
    'latitude': latitude_data,
    'longitude': longitude_data,
    'yield': yield_data
})

print('Nuclear Data:\n')
print(data)

Nuclear Data:

       country          name      series  latitude  longitude  yield
0          USA          Able  Crossroads     11.59     165.50   23.0
1          USA         Baker  Crossroads     11.59     165.50   23.0
2          USA         X-ray   Sandstone  11.66276  162.23785   37.0
3          USA          Yoke   Sandstone  11.61569   162.3194   49.0
4          USA         Zebra   Sandstone   11.5352  162.36063   18.0
...        ...           ...         ...       ...        ...    ...
1903  Pakistan  Chagai 1 - 1         N/A  28.79273   64.94565   32.0
1904  Pakistan  Chagai 1 - 2         N/A  28.79273   64.94565    1.0
1905  Pakistan  Chagai 1 - 3         N/A  28.79273   64.94565    1.0
1906  Pakistan  Chagai 1 - 4         N/A  28.79273   64.94565    1.0
1907  Pakistan  Chagai 1 - 5         N/A  28.79273   64.94565    1.0

[1908 rows x 6 columns]


In [53]:
# Make an empty map
m = folium.Map(location=[20,0], tiles="OpenStreetMap", zoom_start=1)

# Add circle marker for each test onto the map
for i in range(0,len(data)):
    label = '<b>Country:</b> %s <br> <b>Name:</b> %s <br> <b>Series:</b> %s <br> <b>Location:</b> %s\n, %s <br> <b>Yield:</b> %s kt' % (data.iloc[i]['country'], data.iloc[i]['name'], data.iloc[i]['series'], data.iloc[i]['latitude'], data.iloc[i]['longitude'], data.iloc[i]['yield'],)
    folium.Circle(
      location=[data.iloc[i]['latitude'], data.iloc[i]['longitude']],
      popup=folium.Popup(label, max_width=500),
      radius=float(data.iloc[i]['yield']*25),
      color='crimson',
      fill=True,
      fill_color='crimson'
    ).add_to(m)

display(m)

In [51]:
def calc_lat_antipode(latitude):
    latitude = float(latitude)
    return latitude*-1

def calc_lon_antipode(longitude):
    longitude = float(longitude)
    if longitude >= 0: 
        return longitude - 180
    else:
        return longitude + 180
    
antipode_data = pd.DataFrame({
    'country': country_data,
    'name': name_data,
    'series': series_data,
    'latitude': map(calc_lat_antipode, latitude_data),
    'longitude': map(calc_lon_antipode, longitude_data),
    'yield': yield_data
})

print('Antipodes of Nuclear Data:\n')
print(antipode_data)

Antipodes of Nuclear Data:

       country          name      series  latitude  longitude  yield
0          USA          Able  Crossroads -11.59000  -14.50000   23.0
1          USA         Baker  Crossroads -11.59000  -14.50000   23.0
2          USA         X-ray   Sandstone -11.66276  -17.76215   37.0
3          USA          Yoke   Sandstone -11.61569  -17.68060   49.0
4          USA         Zebra   Sandstone -11.53520  -17.63937   18.0
...        ...           ...         ...       ...        ...    ...
1903  Pakistan  Chagai 1 - 1         N/A -28.79273 -115.05435   32.0
1904  Pakistan  Chagai 1 - 2         N/A -28.79273 -115.05435    1.0
1905  Pakistan  Chagai 1 - 3         N/A -28.79273 -115.05435    1.0
1906  Pakistan  Chagai 1 - 4         N/A -28.79273 -115.05435    1.0
1907  Pakistan  Chagai 1 - 5         N/A -28.79273 -115.05435    1.0

[1908 rows x 6 columns]


In [54]:
m = folium.Map(location=[20,0], tiles="OpenStreetMap", zoom_start=1)

# Add circle marker for each test onto the map
for i in range(0,len(antipode_data)):
    label = '<b>Country:</b> %s <br> <b>Name:</b> %s <br> <b>Series:</b> %s <br> <b>Location:</b> %s\n, %s <br> <b>Yield:</b> %s kt' % (antipode_data.iloc[i]['country'], antipode_data.iloc[i]['name'], antipode_data.iloc[i]['series'], antipode_data.iloc[i]['latitude'], antipode_data.iloc[i]['longitude'], antipode_data.iloc[i]['yield'],)
    folium.Circle(
      location=[antipode_data.iloc[i]['latitude'], antipode_data.iloc[i]['longitude']],
      popup=folium.Popup(label, max_width=500),
      radius=float(antipode_data.iloc[i]['yield']*25),
      color='blue',
      fill=True,
      fill_color='blue'
    ).add_to(m)

display(m)